Before start, make sure your cluster has installed the anaconda parallel package, and use interactive nodes to start engines.

Now we use mass and radii table by Audi etc, and Angeli, etc

In [ ]:
import numpy as np
from nuclear_data import audi2003, audi2012, angeli2013

In [ ]:
Nns, Nps, E_exps = np.asarray(audi2012.data).T[:3]
Nns = np.array([Nn.real for Nn in Nns])
Nps = np.array([Np.real for Np in Nps])
Aas = Nns+Nps
#ind = np.where(np.logical_and(Nns + Nps >= 16, E_exps.imag < 0.2))
ind = np.where(Nns + Nps >= 16)
Nns = Nns[ind]; Nps = Nps[ind]; E_exps = E_exps[ind]
Nns_r, Nps_r, R_exps = np.asarray(angeli2013.data).T[:3]
Nns_r = np.array([Nn.real for Nn in Nns_r])
Nps_r = np.array([Np.real for Np in Nps_r])
intersections = [];
for i in range(len(Nns_r)):
    Nn = Nns_r[i]; Np = Nps_r[i]; R = R_exps[i];
    a = np.where([Nns[j] == Nn and Nps[j] == Np for j in range(len(Nns))])
    if np.shape(a[0]) == (1,):
        aa = a[0][0]
        intersections.append([aa, i])

In [ ]:
import nuclei
p = nuclei.SphericalNuclearProblem(N=500, R=25.0, evolver_type='abm', form_factors=['n','p'])

In [ ]:
from IPython.parallel import Client
rc1 = Client()
print len(rc1)

## Fit 

Here is the main body of the fit function, which calculate the wave function, binding energy for the nucleus with specific neutron number and proton number, in given set of NEDF parameters.

In [ ]:
%%px 
#use magic function to execute on each engines
import time
import nuclei_gradient4 as nuclei
import numpy as np
nuclei.superfluid.utils.set_num_threads(1)
params = [-738.431910742, 934.854779091, 136.813604927, -159.026304997, 0.466590487878, 11.4048358879]
p = nuclei.SphericalNuclearProblem(N=500, R=20.0, evolver_type='abm', form_factors=['n','p'])
def solve(Nn, Np, psi0=None):
    global params, p
    b0, c0, a1, b1, eta_t, delta  = params
    p.functional_params.b_0 = b0
    p.functional_params.c_0 = c0
    p.functional_params.a_1 = a1
    p.functional_params.b_1 = b1
    p.functional_params.lam = eta_t
    p.functional_params.delta = delta;
    #p.functional_params.alpha = alpha;
    p.init()
    Aa = Nn + Np
    R = 4.00*Aa**(1./3.)
    #R = 25.00   # proved to be a good system size for infrared convergence
    p.R = R; p.init()
    p.model.Nn = Nn; p.model.Np = Np
    psi = None
    if psi0 is not None:
        psi0 = np.copy(psi0)
    for ntry in range(10):
        try:
            psi = nuclei.solve(p, psi0=psi0)
            break
        except ValueError:
            print("radii changes for solving psi")
            R += 1.0
            p.R = R; p.init()
            p.model.Nn = Nn; p.model.Np = Np
    #for some bad nuclei (very few), use smaller box for better convergence
    if psi is  None:
        R = 4.00*Aa**(1./3.)
        p.R = R; p.init()
        p.model.Nn = Nn; p.model.Np = Np
        for ntry in range(10):
            try:
                psi = nuclei.solve(p, psi0=psi0)
                break
            except ValueError:
                print("radii changes for solving psi")
                R += 1.0
                p.R = R; p.init()
                p.model.Nn = Nn; p.model.Np = Np

    #--get energy and radii--------------------
    energy = p.model.get_energy(psi,t=0)
    energy = abs(energy)
    rms_c = p.model.get_rc_exact(psi)
    return energy, psi, rms_c, R

In [ ]:
#rc[:]['params'] = [-712.003250031, 881.03984528, 136.665030794, -159.514379479, 0.466590487878, 11.4048358879, -40.2366007665, 88.0994559594, -41.8245659985]
rc1[:]['p'] = p
psi0s = {}
Rs = {}
dview = rc1[:]
N1 = len(Nns); N2 = len(intersections)
rc1[:]['N1'] = N1; rc1[:]['N2'] = N2
def get_energy_err(Nn, Np, E_exp, psi):
    #tic = time.time()
    E, psi, rms_c, R = solve(Nn, Np, psi)
    err = (E - E_exp.real)/np.sqrt(N1)
    #toc = time.time() - tic
    #return (err, toc, psi)
    return (err, psi, rms_c, R)

#def get_radii_err(Nn, Np, R_exp, psi):
#    E, psi, rms = solve(Nn, Np, psi)
#    err = 3*(rms - R_exp)/np.sqrt(N2)/0.05
#    return (err, psi)
#def psi_init(Nns, Nps, view = dview):
#    global psis_1, psi0s_2
#    psis = 
def err(Nns, Nps, E_exps, Nns_r, Nps_r, R_exps, view=dview, rfit=False):
    global psi0s
    psis = [psi0s.get((Nn, Np), None) for Nn, Np in zip(Nns, Nps)]
    res = view.map(get_energy_err, Nns, Nps, E_exps, psis, block=True)    
    ans = []; rms_cs = []; 
    for _n, _k in enumerate(zip(Nns, Nps)):
        psi0s[_k] = res[_n][1]
        ans.append(res[_n][0])
        rms_cs.append(res[_n][2])
        Rs[_k] = res[_n][3]
    #psis = [psi0s_2.get((Nn, Np), None) for Nn, Np in zip(Nns_r, Nps_r)]
    #res2 = view.map(get_radii_err, Nns_r, Nps_r, R_exps, psis, block=True) 
    #for _n, _k in enumerate(zip(Nns_r, Nps_r)):
    #    psi0s_2[_k] = res2[_n][1]
    #    ans.append(res2[_n][0])
    for intersection in intersections:
        i, j = intersection
        rmsc_t = rms_cs[i]
        rmsc_e = R_exps[j].real
        err = 3*(rmsc_t - rmsc_e)/np.sqrt(N2)/0.05
        ans.append(err)
    return ans

In [ ]:
import numpy as np
def func(beta, rfit = False):
    global psi0s
    rc1[:]['params'] = beta
    errors = err(Nns, Nps, E_exps, Nns_r, Nps_r, R_exps, view=rc1.load_balanced_view(), rfit = rfit)
    errors = np.asarray(errors)
    energy_dev = np.sqrt((errors[:N1]**2).sum())
    radii_dev = np.sqrt((errors[N1:]**2*0.05**2/3**2).sum())
    er_dev = np.sqrt((errors**2).sum())
    
    psi_Ca = psi0s.get((28,20),None)
    psi_Ca = nuclei.solve(p, psi0=psi_Ca)
    R = Rs.get((28,20),None)
    p.R = R; p.init()
    nskin_Ca = p.model.get_neutron_skin(psi_Ca)
    
    psi_Pb = psi0s.get((126,82),None)
    R = Rs.get((126,82),None)
    p.R = R; p.init()
    p.model.Nn = 126; p.model.Np = 82
    psi_Pb = nuclei.solve(p, psi0=psi_Pb)
    nskin_Pb = p.model.get_neutron_skin(psi_Pb)
    print("b0: {0}, c0: {1}, a1: {2}, b1: {3}, eta_t: {4}, delta: {5}, rms_energy: {6} MeV, rms_radii: {7}, chi: {8}, nskin_Ca: {9}, nskin_Pb: {10}"
          .format(beta[0], beta[1], beta[2], beta[3], beta[4], beta[5], energy_dev, radii_dev, er_dev, nskin_Ca, nskin_Pb))#, ))
    if rfit == True:
        return errors
    if rfit == False:
        return errors[:N1]

In [ ]:
import scipy as sp
beta0 = [-738.301703092, 934.375547305, 122.585233653, -127.96402741, 0.474192583538, 11.4716045194]
beta, cov_a, infodict, msg, ier = sp.optimize.leastsq(func, beta0, xtol = 1e-6, ftol = 1e-5, full_output=True)

## Output

In [ ]:
%%px 
#use magic function to execute on each engines
import time
import nuclei_gradient4 as nuclei
import numpy as np
nuclei.superfluid.utils.set_num_threads(1)
params = [0.0, -738.431910742, 934.854779091, 136.813604927, -159.026304997, 0.0, 0.466590487878, 11.4048358879]
p = nuclei.SphericalNuclearProblem(N=500, R=20.0, evolver_type='abm', form_factors=['n','p'])
def solve(Nn, Np, psi0=None):
    global params, p
    b0, c0, a1, b1, eta_t, delta = params
    p.functional_params.a_0 = 0.0;
    p.functional_params.b_0 = b0
    p.functional_params.c_0 = c0
    p.functional_params.a_1 = a1
    p.functional_params.b_1 = b1
    p.functional_params.c_1 = 0.0;
    p.functional_params.a_2 = 0.;
    p.functional_params.b_2 = 0.;
    p.functional_params.c_2 = 0.;
    p.functional_params.lam = eta_t
    p.functional_params.delta = delta;
    p.functional_params.alpha = 0.0;
    p.init()
    Aa = Nn + Np
    R = 4.00*Aa**(1./3.)
    #R = 25.00   # proved to be a good system size for infrared convergence
    p.R = R; p.init()
    p.model.Nn = Nn; p.model.Np = Np
    psi = None
    if psi0 is not None:
        psi0 = np.copy(psi0)
    for ntry in range(10):
        try:
            psi = nuclei.solve(p, psi0=psi0)
            break
        except ValueError:
            print("radii changes for solving psi")
            R += 1.0
            p.R = R; p.init()
            p.model.Nn = Nn; p.model.Np = Np
    #for some bad nuclei (very few), use smaller box for better convergence
    if psi is  None:
        R = 4.00*Aa**(1./3.)
        p.R = R; p.init()
        p.model.Nn = Nn; p.model.Np = Np
        for ntry in range(10):
            try:
                psi = nuclei.solve(p, psi0=psi0)
                break
            except ValueError:
                print("radii changes for solving psi")
                R += 1.0
                p.R = R; p.init()
                p.model.Nn = Nn; p.model.Np = Np

    #--get energy and radii--------------------
    energy = p.model.get_energy(psi,t=0)
    energy = abs(energy)
    rho_n, rho_p = p.model.get_rhos(psi)
    rms_c = p.model.get_rc_exact(psi)
    rms_n = p.model.get_rms_radii(rho_n)
    rms_p = p.model.get_rms_radii(rho_p)
    return psi, energy, rms_n, rms_p, rms_c,R

In [ ]:
#beta =[-739.482816694, 934.170382743, 3.12324576859, 138.61309918, 11.4194466155]
rc1[:]['params'] = beta
#rc1[:]['p'] = p
dview = rc1[:]
psi0s = {}
#psi0s_2 = {}
N1 = len(Nns); N2 = len(intersections)
rc1[:]['N1'] = N1; rc1[:]['N2'] = N2
def get_energy_err(Nn, Np, E_exp, psi):
    #tic = time.time()
    psi, E_th, rms_n, rms_p, rms_c, R = solve(Nn, Np, psi)
    err = (E_th - E_exp.real)/np.sqrt(N1)
    return (err, psi, E_th, rms_n, rms_p, rms_c, R)

def get_export(Nns, Nps, E_exps, Nns_r, Nps_r, R_exps, view=dview):
    global psi0s
    psis = [psi0s.get((Nn, Np), None) for Nn, Np in zip(Nns, Nps)]
    res1 = view.map(get_energy_err, Nns, Nps, E_exps, psis, block=True)    
    ans = []; E_ths = []; rms_ns = []; rms_ps = []; rms_cs = [];
    psi_fs = []; Rs = []
    for _n, _k in enumerate(zip(Nns, Nps)):
        psi0s[_k] = res1[_n][1]
        ans.append(res1[_n][0])
        E_ths.append(res1[_n][2])
        rms_ns.append(res1[_n][3])
        rms_ps.append(res1[_n][4])
        rms_cs.append(res1[_n][5])
        Rs.append(res1[_n][6])
        psi_fs.append(res1[_n][1])
        
    for intersection in intersections:
        i, j = intersection
        rmsc_t = rms_cs[i]
        rmsc_e = R_exps[j].real
        err = (rmsc_t - rmsc_e)/np.sqrt(N2)
        ans.append(err)
    return ans, E_ths, rms_ns, rms_ps, rms_cs, Rs, psi_fs

In [ ]:
errors, E_ths, rms_ns, rms_ps, rms_cs, Rs, psi_fs = get_export(Nns, Nps, E_exps, Nns_r, Nps_r, R_exps, view=rc1.load_balanced_view())
errors = np.asarray(errors)
energy_dev = np.sqrt((errors[:N1]**2).sum())
radii_dev = np.sqrt((errors[N1:]**2).sum())
energy_dev, radii_dev

In [ ]:
import shi_utils

In [ ]:
shi_utils.write_to_txt("NEDF-1", beta, Nns, Nps, rms_ns, rms_ps, rms_cs, energy_dev, radii_dev, E_exps, E_ths, cov)